# Projeto de Machine Learning - Classificação Estelar

Na astronomia, a classificação estelar é a classificação de estrelas com base em suas características espectrais. O esquema de classificação de galáxias, quasares e estrelas é um dos mais fundamentais na astronomia. O catálogo inicial de estrelas e sua distribuição no céu levou à compreensão de que elas compõem nossa própria galáxia e, após a distinção de que Andrômeda era uma galáxia separada da nossa, várias galáxias começaram a ser pesquisadas à medida que telescópios mais poderosos foram construídos. Este conjunto de dados tem como objetivo classificar estrelas, galáxias e quasares com base em suas características espectrais.

Conteúdo:
Os dados consistem em 100.000 observações do espaço feitas pelo SDSS (Sloan Digital Sky Survey). Cada observação é descrita por 17 colunas de características e 1 coluna de classe que a identifica como estrela, galáxia ou quasar.

- obj_ID = Identificador de objeto, o valor único que identifica o objeto no catálogo de imagens usado pelo CAS
- alpha = Ângulo de ascensão reta (no equinócio J2000)
- delta = Ângulo de declinação (no equinócio J2000)
- u = Filtro ultravioleta no sistema fotométrico
- g = Filtro verde no sistema fotométrico
- r = Filtro vermelho no sistema fotométrico
- i = Filtro infravermelho próximo no sistema fotométrico
- z = Filtro infravermelho no sistema fotométrico
- run_ID = Número de execução usado para identificar a varredura específica
- rereun_ID = Número de repetição para especificar como a imagem foi processada
- cam_col = Coluna da câmera para identificar a linha de varredura dentro da execução
- field_ID = Número do campo para identificar cada campo
- spec_obj_ID = ID único usado para objetos espectroscópicos ópticos (isso significa que 2 observações diferentes com o mesmo spec_obj_ID devem compartilhar a classe de saída)
- classe = classe do objeto (galáxia, estrela ou quasar)
- redshift = valor de desvio para o vermelho com base no aumento no comprimento de onda
- plate = ID do prato, que identifica cada prato no SDSS
- MJD = Data Juliana Modificada, usada para indicar quando um determinado conjunto de dados do SDSS foi obtido
- fiber_ID = ID da fibra que identifica a fibra que apontou a luz para o plano focal em cada observação

## 0.1 Importação das bibliotecas e limpeza

In [272]:
import numpy as np
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go

from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import LabelEncoder
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score

In [240]:
data = pd.read_csv("./data/star_classification.csv")
data = data[(data['u'] > 0)]

In [241]:
data.head()

obj_ID       alpha      delta         u         g         r  \
0  1.237661e+18  135.689107  32.494632  23.87882  22.27530  20.39501   
1  1.237665e+18  144.826101  31.274185  24.77759  22.83188  22.58444   
2  1.237661e+18  142.188790  35.582444  25.26307  22.66389  20.60976   
3  1.237663e+18  338.741038  -0.402828  22.13682  23.77656  21.61162   
4  1.237680e+18  345.282593  21.183866  19.43718  17.58028  16.49747   

          i         z  run_ID  rerun_ID  cam_col  field_ID   spec_obj_ID  \
0  19.16573  18.79371    3606       301        2        79  6.543777e+18   
1  21.16812  21.61427    4518       301        5       119  1.176014e+19   
2  19.34857  18.94827    3606       301        2       120  5.152200e+18   
3  20.50454  19.25010    4192       301        3       214  1.030107e+19   
4  15.97711  15.54461    8102       301        3       137  6.891865e+18   

    class  redshift  plate    MJD  fiber_ID  
0  GALAXY  0.634794   5812  56354       171  
1  GALAXY  0.779136  10445  58158       427  
2  GALAXY  0.644195   4576  55592       299  
3  GALAXY  0.932346   9149  58039       775  
4  GALAXY  0.116123   6121  56187       842

In [242]:
colunas = data.columns
colunas = [coluna  for coluna in colunas if("ID" not in coluna)]
data = data[colunas]
del data['cam_col']
del data['plate']
del data['MJD']
colunafinal = 'class'
colunas = [i for i in data.columns if(i!= colunafinal)] + [colunafinal]
data = data[colunas]

In [293]:
data.head()

alpha      delta         u         g         r         i         z  \
0  135.689107  32.494632  23.87882  22.27530  20.39501  19.16573  18.79371   
1  144.826101  31.274185  24.77759  22.83188  22.58444  21.16812  21.61427   
2  142.188790  35.582444  25.26307  22.66389  20.60976  19.34857  18.94827   
3  338.741038  -0.402828  22.13682  23.77656  21.61162  20.50454  19.25010   
4  345.282593  21.183866  19.43718  17.58028  16.49747  15.97711  15.54461   

   redshift   class  
0  0.634794  GALAXY  
1  0.779136  GALAXY  
2  0.644195  GALAXY  
3  0.932346  GALAXY  
4  0.116123  GALAXY

## 1.1 Visualização dos dados

In [296]:
classes_unicas = data['class'].unique()
fig = go.Figure()
# Criar um histograma para cada classe
for classe in classes_unicas:
    classe_data = data[data['class'] == classe]
    trace = go.Histogram(x=classe_data['alpha'], name=f'{classe}', histnorm='probability density')
    fig.add_trace(trace)

fig.update_layout(title="Distribuição de ângulos")
fig.show()

In [297]:
classes_unicas = data['class'].unique()
fig = go.Figure()
# Criar um histograma para cada classe
for classe in classes_unicas:
    classe_data = data[data['class'] == classe]
    trace = go.Histogram(x=classe_data['u'], name=f'{classe}', histnorm='probability density')
    fig.add_trace(trace)

fig.update_layout(title="Histogramas do Ultravioleta")
fig.show()

In [298]:
classes_unicas = data['class'].unique()
fig = go.Figure()
# Criar um histograma para cada classe
for classe in classes_unicas:
    classe_data = data[data['class'] == classe]
    trace = go.Histogram(x=classe_data['g'], name=f'{classe}', histnorm='probability density')
    fig.add_trace(trace)

fig.update_layout(
    title="Histogramas para Classes",
    
)
fig.show()

In [299]:
classes_unicas = data['class'].unique()
fig = go.Figure()
# Criar um histograma para cada classe
for classe in classes_unicas:
    classe_data = data[data['class'] == classe]
    trace = go.Histogram(x=classe_data['r'], name=f'{classe}', histnorm='probability density')
    fig.add_trace(trace)

fig.update_layout(title="Histogramas para Classes")
fig.show()

In [279]:
categorias, valores = np.unique(data['class'].values,return_counts=True)
# Crie o gráfico de barras
valores = valores/np.sum(valores)
fig = go.Figure(
    data=go.Bar(
        x=categorias[np.argsort(valores)[::-1]], 
        y=valores[np.argsort(valores)[::-1]],
        text = np.round(valores[np.argsort(valores)[::-1]],3),
        marker_color=cores
        )
    )

# Personalize o layout do gráfico de barras
fig.update_layout(
    xaxis_title="Categorias",
    yaxis_title="Valores",
    xaxis = dict(tickfont=dict(size=15)),
    yaxis = dict(tickfont=dict(size=15)),
    width=800,  # Largura do gráfico em pixels
    height=800,
    font=dict(
        #family="Courier New, monospace",
        size=20,
        #color="RebeccaPurple"
    ),
)
s = 20
fig.update_layout(margin=dict(l=s, r=s, t=s, b=s))
# Exiba o gráfico de barras
fig.show()


In [244]:
correlacao = data.iloc[:,:-1].corr()
fig = px.imshow(correlacao,x =  correlacao.columns,y = correlacao.columns,color_continuous_scale="Cividis_r")

# Personalize o layout do heatmap
fig.update_layout(
    xaxis = dict(title = "Variáveis",tickfont=dict(size=15)),
    yaxis = dict(title = "Variáveis",tickfont=dict(size=15)),
    width=800,  # Largura do gráfico em pixels
    height=800,
    font=dict(
        #family="Courier New, monospace",
        size=20,
        #color="RebeccaPurple"
    ),
)
correlacao = correlacao.values
for i in range(len(correlacao)):
    for j in range(len(correlacao[i])):
        fig.add_annotation(
            text=round(correlacao[i][j],2), 
            x=j, 
            y=i, 
            xref="x", 
            yref="y",
            showarrow=False, 
            font=dict(color="white" if correlacao[i][j] > 0.5 else "black")
        )


s = 10
fig.update_layout(margin=dict(l=s, r=s, t=s, b=s))
# Exiba o heatmap
fig.show()

## 1.3 Algoritmos para previsão.

In [303]:
x = data.iloc[:,:-1]
y = data['class'].values
scaler = StandardScaler()
scaler.fit(x)
x = scaler.transform(x)

X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

## 1.3.1 Regressão Logística

In [304]:
model = LogisticRegression(
        multi_class='multinomial', 
        solver='lbfgs',
        max_iter=1000,
        tol = 1e-9
    )
# fit the model on the whole dataset
model.fit(X_train, y_train)

LogisticRegression(max_iter=1000, multi_class='multinomial', tol=1e-09)

In [155]:
def conf_matrix(modelo,x,y):
    predictions = modelo.predict(x)
    # Calcular a matriz de confusão
    confusion = confusion_matrix(y, predictions)
    confusion = confusion/np.sum(confusion,axis = 1)[:, np.newaxis]
    class_labels = modelo.classes_

    fig = px.imshow(confusion,
                    x=class_labels,
                    y=class_labels,
                    color_continuous_scale='Cividis_r')

    # Personalizar o layout do gráfico
    fig.update_layout(
        xaxis_title="Classe Prevista",
        yaxis_title="Classe Real"
    )
    annotations = []
    for i in range(len(class_labels)):
        for j in range(len(class_labels)):
            annotations.append(dict(x=class_labels[j],
                                    y=class_labels[i],
                                    text=str(np.round(confusion[i, j], 4)),
                                    showarrow=False,
                                    font=dict(color='white' if confusion[i, j] > np.max(confusion)/3 else 'black')))
    fig.update_layout(width=800, height=600,template = 'simple_white',annotations=annotations,)
    s = 10
    fig.update_layout(margin=dict(l=s, r=s, t=s, b=s))
    # Mostrar o gráfico
    acc= np.trace(confusion)/np.sum(confusion)
    precision = confusion[0][0]/np.sum(confusion[0])
    sensitive = confusion[0][0]/np.sum(confusion[:,0])
    print(f"Acurácia: {acc}")
    print(f"Precisão = {precision}")
    print(f"Sensitibilidade = {sensitive}")
    print(f"F1_score = {2*(precision*sensitive)/(precision+sensitive)}")
    fig.show()

In [308]:
conf_matrix(model,X_test,y_test)

Acurácia: 0.9471029841854559
Precisão = 0.9637936827956989
Sensitibilidade = 0.8880304809380167
F1_score = 0.9243622417502468


In [310]:
# Crie um classificador k-NN
k = 3  # Número de vizinhos
knn = KNeighborsClassifier(n_neighbors=k)

# Treine o modelo
knn.fit(X_train, y_train)

KNeighborsClassifier(n_neighbors=3)

In [311]:
conf_matrix(knn,X_test,y_test)

Acurácia: 0.9294055993315298
Precisão = 0.9542170698924731
Sensitibilidade = 0.8562277437766487
F1_score = 0.902570597743188


In [313]:
from sklearn.naive_bayes import GaussianNB
naive_bayes = GaussianNB()

# Treine o modelo
naive_bayes.fit(X_train, y_train)

GaussianNB()

In [314]:
conf_matrix(naive_bayes,X_test,y_test)

Acurácia: 0.9255224393767213
Precisão = 0.9131384408602151
Sensitibilidade = 0.8747570585785236
F1_score = 0.8935357763947775


In [370]:
indice_variavel = 0

# Estime o coeficiente do modelo.
coeficiente = model.coef_[0][indice_variavel]  # Substitua [0] pelo índice da classe desejada.

# Obtenha o desvio padrão do coeficiente usando a biblioteca numpy.
desvio_padrao_coef = np.std(X_train[:, indice_variavel])

# Calcule a estatística de teste de Wald.
estatistica_wald = coeficiente / desvio_padrao_coef

# Graus de liberdade para o teste de Wald (geralmente, o número de observações menos o número de parâmetros estimados).
graus_de_liberdade = X_train.shape[0] - X_train.shape[1]

# Calcule o valor-p associado ao teste de Wald.
from scipy.stats import norm
valor_p = 2 * (1 - norm.cdf(abs(estatistica_wald)))

# Imprima o valor-p.
nivel_de_significancia = 0.05

if valor_p < nivel_de_significancia:
    print("O coeficiente é estatisticamente significativo.")
else:
    print("O coeficiente não é estatisticamente significativo.")


O coeficiente não é estatisticamente significativo.


In [173]:
from scipy.stats import chi2
from statsmodels.discrete.discrete_model import MNLogit

model_mnlogit = MNLogit(y, x)
model_mnlogit = model_mnlogit.fit(disp=0)  # ajuste do modelo

LLR = 2 * (model_mnlogit.llf - model_mnlogit.llnull)
df = model_mnlogit.df_model
p_valor = 1 - chi2.cdf(LLR, df)

print("Estatística de Teste:", LLR)
print("Graus de Liberdade:", df)
print("Valor-p:", p_valor)
if(p_valor < 0.05):
    print("Existe um coefiente diferente de 0")
else:
    print("Todos os coeficientes são 0.")

Estatística de Teste: 72870.50118980715
Graus de Liberdade: 14.0
Valor-p: 0.0
Existe um coefiente diferente de 0


In [362]:
x = data[['alpha','delta','redshift']].values
y = data['class'].values
scaler = StandardScaler()
scaler.fit(x)
x = scaler.transform(x)

In [363]:
model = LogisticRegression(multi_class='multinomial', solver='lbfgs',max_iter=1000)
# fit the model on the whole dataset
model.fit(x, y)

LogisticRegression(max_iter=1000, multi_class='multinomial')

In [364]:
conf_matrix(model,x,y)

Acurácia: 0.9196373175025879
Precisão = 0.9659685423500715
Sensitibilidade = 0.8239294817125944
F1_score = 0.8893131896337575
